In [1]:
import torch
import torchvision
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
import torch.nn as nn
import torch.nn.functional as F
from torchvision.datasets import MNIST
from torchvision.transforms import ToTensor
from torchvision.utils import make_grid
from torch.utils.data.dataloader import DataLoader
from torch.utils.data import random_split
import pickle

from scipy import stats
    
from torchsummary import summary
import math
import random
import pandas as pd

from sklearn.model_selection import train_test_split

In [2]:
def get_default_device():
    """Pick GPU if available, else CPU"""
    if torch.cuda.is_available():
        return torch.device('cuda')
    else:
        return torch.device('cpu')
    
def to_device(data, device):
    """Move tensor(s) to chosen device"""
    if isinstance(data, (list,tuple)):
        return [to_device(x, device) for x in data]
    return data.to(device, non_blocking=True)



class DeviceDataLoader():
    """Wrap a dataloader to move data to a device"""
    def __init__(self, dl, device):
        self.dl = dl
        self.device = device
        
    def __iter__(self):
        """Yield a batch of data after moving it to device"""
        for b in self.dl: 
            yield to_device(b, self.device)

    def __len__(self):
        """Number of batches"""
        return len(self.dl)


In [3]:
print("Program To train a base neuron for Pima")

print("Torch cuda ",torch.cuda.is_available())


device = get_default_device()
print("device ",device)


Program To train a base neuron for Pima
Torch cuda  False
device  cpu


In [4]:
df=pd.read_csv("pima-indians-diabetes.data.csv",header=None)
print(df.head())

   0    1   2   3    4     5      6   7  8
0  6  148  72  35    0  33.6  0.627  50  1
1  1   85  66  29    0  26.6  0.351  31  0
2  8  183  64   0    0  23.3  0.672  32  1
3  1   89  66  23   94  28.1  0.167  21  0
4  0  137  40  35  168  43.1  2.288  33  1


In [5]:
X=df.loc[:,:7].values
y=df.loc[:,8].values

In [6]:
X.shape

(768, 8)

In [7]:
y.shape

(768,)

In [8]:

X_train,X_test,y_train,y_test = train_test_split(X,y , test_size =0.2,random_state=0)



In [50]:
# Creating Tensors
X_train=torch.FloatTensor(X_train)
X_test=torch.FloatTensor(X_test)
y_train=torch.LongTensor(y_train)
y_test=torch.LongTensor(y_test)

In [162]:


def evaluate(model, X_test, y_test):
    """Evaluate the model's performance on the validation set"""
    outputs = [model.validation_step(X_test,y_test)]
#     print("outputs are ",outputs)
    return model.validation_epoch_end(outputs)

def accuracy(outputs, labels):
    _, preds = torch.max(outputs, dim=1)
    return torch.tensor(torch.sum(preds == labels).item() / len(preds))        


def correct(output, target, topk=(1,)):
    """Computes how many correct outputs with respect to targets

    Does NOT compute accuracy but just a raw amount of correct
    outputs given target labels. This is done for each value in
    topk. A value is considered correct if target is in the topk
    highest values of output.
    The values returned are upperbounded by the given batch size

    [description]

    Arguments:
        output {torch.Tensor} -- Output prediction of the model
        target {torch.Tensor} -- Target labels from data

    Keyword Arguments:
        topk {iterable} -- [Iterable of values of k to consider as correct] (default: {(1,)})

    Returns:
        List(int) -- Number of correct values for each topk
    """

    with torch.no_grad():
        maxk = max(topk)
        # Only need to do topk for highest k, reuse for the rest
        _, pred = output.topk(k=maxk, dim=1, largest=True, sorted=True)
        pred = pred.t()
        correct = pred.eq(target.view(1, -1).expand_as(pred))

        res = []
        for k in topk:
            correct_k = correct[:k].reshape(-1).float().sum(0, keepdim=True)
            res.append(torch.tensor(correct_k.item()))
        return res

class PIMANet(nn.Module):
    """Feedfoward neural network with 1 hidden layer"""
    def __init__(self):
        super().__init__()        
        self.fc1 = nn.Linear(8, 2)          


        
    def forward(self, x):
        x = x.view(x.shape[0], -1)
        x = self.fc1(x)
#         x = F.relu(self.fc1(x))
        return x
        
        
    
    def training_step(self, X_train, y_train):

        out = self(X_train)                  # Generate predictions
        loss = F.cross_entropy(out, y_train) # Calculate loss
        return loss
    
    def validation_step(self, X_test, y_test):
        
        out = self(X_test)                    # Generate predictions
        loss = F.cross_entropy(out, y_test)   # Calculate loss
        acc = accuracy(out, y_test)           # Calculate accuracy
        top_1, top_5 = correct(out, y_test,topk=(1,2))
#         print("Batch is ",batch[1].shape)
        
        top_1=top_1/X_test.shape[0]
        top_5=top_5/X_test.shape[0]

#         print("corr",top_1,top_5)
#         return {'val_loss': loss, 'val_acc': acc}
        return {'val_loss': loss, 'val_acc': acc, 'top_1': top_1, 'top_5': top_5}
        
    def validation_epoch_end(self, outputs):
        batch_losses = [x['val_loss'] for x in outputs]
        epoch_loss = torch.stack(batch_losses).mean()   # Combine losses
        batch_accs = [x['val_acc'] for x in outputs]
        epoch_acc = torch.stack(batch_accs).mean()      # Combine accuracies
        
        batch_top_1s = [x['top_1'] for x in outputs]
#         print(batch_top_1s)
        epoch_top_1 = torch.stack(batch_top_1s).mean()      # Combine top_1
        
        batch_top_5s = [x['top_5'] for x in outputs]
        epoch_top_5 = torch.stack(batch_top_5s).mean()      # Combine top_5
        
        return {'val_loss': epoch_loss.item(), 'val_acc': epoch_acc.item(),
               'val_top_1': epoch_top_1.item(), 'val_top_5': epoch_top_5.item()}
    
    def epoch_end(self, epoch, result):
        print("Epoch [{}], val_loss: {:.4f}, val_acc: {:.4f}, val_top_1: {:.4f}, val_top_5: {:.4f}".format(
                                epoch, result['val_loss'], result['val_acc'], 
                                result['val_top_1'], result['val_top_5']))
        
        

        
        


In [189]:
def fit(epochs, lr, model, X_train, y_train, X_test, y_test, opt_func=torch.optim.SGD,
               model_state_path=None):
    print("Op tfn is ",opt_func)
    """Train the model using gradient descent"""
    print("At train")
    history = []
    best_so_far=-999    
    optimizer = opt_func(model.parameters(), lr)
    for epoch in range(epochs):
        loss = model.training_step(X_train,y_train)
#         print(epoch,loss)
        loss.backward()
        optimizer.step()
        optimizer.zero_grad()

        # Validation phase
        result = evaluate(model, X_test, y_test)
        if best_so_far<result["val_top_1"]:
            best_so_far=result["val_top_1"]
            if model_state_path:
                torch.save(model.state_dict(), model_state_path)
        
        model.epoch_end(epoch, result)
        history.append(result)

    return history


In [206]:
torch.manual_seed(20)
model = PIMANet()
model.parameters
if torch.cuda.is_available():
    model=model.cuda()

    
    

print(summary(model, input_size=(1, 8), batch_size=-1))
for nm,params in model.named_parameters():
    print(nm)
    print(params.data)
    
evaluate(model, X_test, y_test)        


epochs=100000
lr=0.0001
model_state_path="model_state/mod_CNN_100000.pt"
history2 = fit(epochs, lr, model, X_train, y_train, X_test, y_test , model_state_path=model_state_path)


----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Linear-1                    [-1, 2]              18
Total params: 18
Trainable params: 18
Non-trainable params: 0
----------------------------------------------------------------
Input size (MB): 0.00
Forward/backward pass size (MB): 0.00
Params size (MB): 0.00
Estimated Total Size (MB): 0.00
----------------------------------------------------------------
None
fc1.weight
tensor([[ 0.0435, -0.2281,  0.2225, -0.1205, -0.1896,  0.2002,  0.2506, -0.2820],
        [-0.2208,  0.3048, -0.2900, -0.1304,  0.3128, -0.1742,  0.1689,  0.0285]])
fc1.bias
tensor([-0.0456, -0.0403])
Op tfn is  <class 'torch.optim.sgd.SGD'>
At train
Epoch [0], val_loss: 33.6828, val_acc: 0.3506, val_top_1: 0.3506, val_top_5: 1.0000
Epoch [1], val_loss: 31.8203, val_acc: 0.3701, val_top_1: 0.3701, val_top_5: 1.0000
Epoch [2], val_loss: 30.0084, val_acc: 0.3831, val_top_1: 0.3831,

Epoch [166], val_loss: 3.0765, val_acc: 0.6623, val_top_1: 0.6623, val_top_5: 1.0000
Epoch [167], val_loss: 3.0724, val_acc: 0.6623, val_top_1: 0.6623, val_top_5: 1.0000
Epoch [168], val_loss: 3.0684, val_acc: 0.6623, val_top_1: 0.6623, val_top_5: 1.0000
Epoch [169], val_loss: 3.0643, val_acc: 0.6623, val_top_1: 0.6623, val_top_5: 1.0000
Epoch [170], val_loss: 3.0602, val_acc: 0.6623, val_top_1: 0.6623, val_top_5: 1.0000
Epoch [171], val_loss: 3.0562, val_acc: 0.6623, val_top_1: 0.6623, val_top_5: 1.0000
Epoch [172], val_loss: 3.0521, val_acc: 0.6623, val_top_1: 0.6623, val_top_5: 1.0000
Epoch [173], val_loss: 3.0480, val_acc: 0.6623, val_top_1: 0.6623, val_top_5: 1.0000
Epoch [174], val_loss: 3.0439, val_acc: 0.6623, val_top_1: 0.6623, val_top_5: 1.0000
Epoch [175], val_loss: 3.0399, val_acc: 0.6623, val_top_1: 0.6623, val_top_5: 1.0000
Epoch [176], val_loss: 3.0358, val_acc: 0.6623, val_top_1: 0.6623, val_top_5: 1.0000
Epoch [177], val_loss: 3.0317, val_acc: 0.6623, val_top_1: 0.6623

Epoch [324], val_loss: 2.4492, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [325], val_loss: 2.4454, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [326], val_loss: 2.4417, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [327], val_loss: 2.4379, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [328], val_loss: 2.4342, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [329], val_loss: 2.4304, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [330], val_loss: 2.4267, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [331], val_loss: 2.4230, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [332], val_loss: 2.4192, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [333], val_loss: 2.4155, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [334], val_loss: 2.4118, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [335], val_loss: 2.4080, val_acc: 0.6558, val_top_1: 0.6558

Epoch [482], val_loss: 1.9045, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [483], val_loss: 1.9014, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [484], val_loss: 1.8983, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [485], val_loss: 1.8953, val_acc: 0.6558, val_top_1: 0.6558, val_top_5: 1.0000
Epoch [486], val_loss: 1.8922, val_acc: 0.6494, val_top_1: 0.6494, val_top_5: 1.0000
Epoch [487], val_loss: 1.8891, val_acc: 0.6494, val_top_1: 0.6494, val_top_5: 1.0000
Epoch [488], val_loss: 1.8861, val_acc: 0.6494, val_top_1: 0.6494, val_top_5: 1.0000
Epoch [489], val_loss: 1.8830, val_acc: 0.6494, val_top_1: 0.6494, val_top_5: 1.0000
Epoch [490], val_loss: 1.8799, val_acc: 0.6494, val_top_1: 0.6494, val_top_5: 1.0000
Epoch [491], val_loss: 1.8769, val_acc: 0.6494, val_top_1: 0.6494, val_top_5: 1.0000
Epoch [492], val_loss: 1.8739, val_acc: 0.6494, val_top_1: 0.6494, val_top_5: 1.0000
Epoch [493], val_loss: 1.8708, val_acc: 0.6494, val_top_1: 0.6494

Epoch [640], val_loss: 1.4817, val_acc: 0.6429, val_top_1: 0.6429, val_top_5: 1.0000
Epoch [641], val_loss: 1.4795, val_acc: 0.6429, val_top_1: 0.6429, val_top_5: 1.0000
Epoch [642], val_loss: 1.4772, val_acc: 0.6429, val_top_1: 0.6429, val_top_5: 1.0000
Epoch [643], val_loss: 1.4750, val_acc: 0.6364, val_top_1: 0.6364, val_top_5: 1.0000
Epoch [644], val_loss: 1.4728, val_acc: 0.6364, val_top_1: 0.6364, val_top_5: 1.0000
Epoch [645], val_loss: 1.4705, val_acc: 0.6364, val_top_1: 0.6364, val_top_5: 1.0000
Epoch [646], val_loss: 1.4683, val_acc: 0.6364, val_top_1: 0.6364, val_top_5: 1.0000
Epoch [647], val_loss: 1.4661, val_acc: 0.6364, val_top_1: 0.6364, val_top_5: 1.0000
Epoch [648], val_loss: 1.4639, val_acc: 0.6429, val_top_1: 0.6429, val_top_5: 1.0000
Epoch [649], val_loss: 1.4617, val_acc: 0.6429, val_top_1: 0.6429, val_top_5: 1.0000
Epoch [650], val_loss: 1.4595, val_acc: 0.6429, val_top_1: 0.6429, val_top_5: 1.0000
Epoch [651], val_loss: 1.4573, val_acc: 0.6429, val_top_1: 0.6429

...

Epoch [99329], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99330], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99331], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99332], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99333], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99334], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99335], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99336], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99337], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99338], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99339], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99340], val_loss: 0.5518, val_acc: 0

Epoch [99482], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99483], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99484], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99485], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99486], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99487], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99488], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99489], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99490], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99491], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99492], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99493], val_loss: 0.5518, val_acc: 0

Epoch [99635], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99636], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99637], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99638], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99639], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99640], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99641], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99642], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99643], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99644], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99645], val_loss: 0.5518, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99646], val_loss: 0.5518, val_acc: 0

Epoch [99788], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99789], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99790], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99791], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99792], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99793], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99794], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99795], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99796], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99797], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99798], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99799], val_loss: 0.5517, val_acc: 0

Epoch [99941], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99942], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99943], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99944], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99945], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99946], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99947], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99948], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99949], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99950], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99951], val_loss: 0.5517, val_acc: 0.7468, val_top_1: 0.7468, val_top_5: 1.0000
Epoch [99952], val_loss: 0.5517, val_acc: 0

In [216]:

if torch.cuda.is_available():
    model.load_state_dict(torch.load(model_state_path))
else:
    model.load_state_dict(torch.load(model_state_path,map_location=torch.device('cpu')))


In [217]:
res = evaluate(model, X_test, y_test)
print("Best Result after training is ",res)


Best Result after training is  {'val_loss': 0.5927060842514038, 'val_acc': 0.7532467246055603, 'val_top_1': 0.7532467246055603, 'val_top_5': 1.0}


In [ ]:
count=0
for nm,params in model.named_parameters():
    print(nm)
    if count==0:
        params.data=torch.tensor([[67.7996, 69.6484, 71.3593, 66.1152, 69.9269, 66.2759, 69.9471, 65.3335],
        [66.2749, 70.3614, 69.0063, 64.3449, 67.6688, 68.5820, 71.7458, 65.5641]])
    print(params.data)
    count+=1


In [218]:
for nm,params in model.named_parameters():
    print(nm)
    print(params.data)


fc1.weight
tensor([[-0.1075,  0.0320, -0.0185, -0.1279,  0.0614,  0.0142,  0.2466, -0.1272],
        [-0.0698,  0.0446, -0.0489, -0.1230,  0.0617,  0.0118,  0.1728, -0.1263]])
fc1.bias
tensor([-0.0235, -0.0624])


In [211]:
print(X_train[0],"\n",y_train[0])
val=X_train[0:1]
out=model(val)
print("out = ",out)
loss = F.cross_entropy(out, y_train[0:1]) 
print("loss=",loss)

tensor([  7.0000, 150.0000,  78.0000,  29.0000, 126.0000,  35.2000,   0.6920,
         54.0000]) 
 tensor(1)
out =  tensor([[33125.3125, 32797.0312]], grad_fn=<AddmmBackward>)
loss= tensor(328.2812, grad_fn=<NllLossBackward>)


In [212]:
print(X_train[1],"\n",y_train[1])
val=X_train[1:2]
out=model(val)
print("out = ",out)
loss = F.cross_entropy(out, y_train[1:2]) 
print("loss=",loss)

tensor([ 4.0000, 97.0000, 60.0000, 23.0000,  0.0000, 28.2000,  0.4430, 22.0000]) 
 tensor(0)
out =  tensor([[16166.5811, 16118.6094]], grad_fn=<AddmmBackward>)
loss= tensor(0., grad_fn=<NllLossBackward>)


In [213]:
res = evaluate(model, X_test, y_test)
print("Result after using the weight from probability notebook ",res)


Result after using the weight from probability notebook  {'val_loss': 80.79315948486328, 'val_acc': 0.7402597665786743, 'val_top_1': 0.7402597665786743, 'val_top_5': 1.0}
